In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{40}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/40)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [-5.013343819985405e-08, -4.2818001262371635e-08, -3.4448243029010667e-08, -2.5230254725111584e-08, -1.5391013815465534e-08, -5.172795065836402e-09, 5.172795065836305e-09], 'solu': -1.9713501349580923e-08}, {'input': [8.432171959533667e-24, 2.5088887820182942e-23, 4.112783199745439e-23, 5.615407245549982e-23, 6.979761328500907e-23, 8.172250523044365e-23, 9.163511787565966e-23], 'solu': 4.387563245781146e-23}, {'input': [-0.03438528645271961, -0.030665664181233045, -0.026190951484099962, -0.021071330638643866, -0.015432863701127375, -0.00941438844055101, -0.0031640996920043714], 'solu': -0.016463952088796655}, {'input': [-5.159259013323586e-19, -4.601157083397439e-19, -3.92975939571317e-19, -3.1615979895827414e-19, -2.315587548206632e-19, -1.412559656399207e-19, -4.747498578345145e-20], 'solu': -2.4702947676718647e-19}, {'input': [2.4060860624183043e-10, 1.935761478426148e-10, 1.417772022411121e-10, 8.648723138887582e-11, 2.906765786518075e-11, -2.906765786518066e-11, -8.6487

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_12.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_12.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_1 delta x=1 20 delta t=1 40")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{40}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/40)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [3.75071397153415e-12, 5.2185853056528465e-12, 6.654282326006483e-12, 8.048953483046874e-12, 9.394000165315643e-12, 1.0681129712743194e-11, 1.1902406543655632e-11], 'solu': 6.288999341446675e-12}, {'input': [9.552200033333743e-22, 9.734122516369293e-22, 9.856030897167227e-22, 9.917173570021265e-22, 9.917173570021265e-22, 9.856030897167227e-22, 9.734122516369295e-22], 'solu': 7.748721393686885e-22}, {'input': [-1.4973307381375582e-13, -2.4852918491128626e-13, -3.4579303093949886e-13, -4.4092494794411795e-13, -5.333384160222378e-13, -6.2246367541256e-13, -7.077512392537874e-13], 'solu': -3.4451394371809525e-13}, {'input': [4.4545271974321616e-13, 4.311858692436726e-13, 4.1426061447639035e-13, 3.94781305265228e-13, 3.7286803802899996e-13, 3.486559153471184e-13, 3.222942130072651e-13], 'solu': 3.08459897806322e-13}, {'input': [-9.06689982945129e-10, -1.0103606150572138e-09, -1.1078020379984748e-09, -1.198413492993916e-09, -1.281636330292124e-09, -1.3569574534267533e-09, -1.42391

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_22.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_22.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_1 delta x=1 40 delta t=1 40")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{40}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/40)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [5.814441242045273e-17, 5.931973455837063e-17, 6.040358996517962e-17, 6.139430741440185e-17, 6.229035929153925e-17, 6.309036394954439e-17, 6.379308783922013e-17], 'solu': 4.797005718954542e-17}, {'input': [-3.302089584108022e-17, -3.20919014318528e-17, -3.111342363668489e-17, -3.008697119741516e-17, -2.9014126829306204e-17, -2.7896544780612285e-17, -2.6735948281848536e-17], 'solu': -2.3508266316261903e-17}, {'input': [3.983153160668599e-20, 3.958452615116792e-20, 3.9276484225468435e-20, 3.890788080790963e-20, 3.84792842582445e-20, 3.799135544128732e-20, 3.744484670790804e-20], 'solu': 3.040042873814746e-20}, {'input': [0.14722558229902602, 0.1569737883975414, 0.1664799522920349, 0.17572941616680177, 0.18470791801896155, 0.19340161364943304, 0.2017970980096857], 'solu': 0.13730507759469324}, {'input': [-6.981315410478196e-22, -7.108873912056451e-22, -7.225471045323777e-22, -7.330927025951806e-22, -7.425079248462005e-22, -7.507782536951554e-22, -7.578909368944059e-22], 'solu':

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_32.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_32.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_1 delta x=1 80 delta t=1 40")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{40}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/40)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [-4.676347218362373e-19, -4.69091317305532e-19, -4.703670691424439e-19, -4.714614855203549e-19, -4.723741445209181e-19, -4.731046942967155e-19, -4.73652853206902e-19], 'solu': -3.683734759059171e-19}, {'input': [1.1323437771784097e-06, 1.1205213730152538e-06, 1.108266986532701e-06, 1.0955853420300135e-06, 1.0824813285225529e-06, 1.0689599978569732e-06, 1.0550265627636354e-06], 'solu': 8.560287382748266e-07}, {'input': [4.343993755767954e-08, 4.4410538807348955e-08, 4.5364018948914885e-08, 4.6300010397632425e-08, 4.72181523109807e-08, 4.8118090727774444e-08, 4.899947870462291e-08], 'solu': 3.6176222848471504e-08}, {'input': [1.3511373241142406e-14, 1.224033642959197e-14, 1.0964580735342468e-14, 9.684597986499171e-15, 8.400881640777315e-15, 7.113926595264857e-15, 5.824228995630127e-15], 'solu': 7.56699991962354e-15}, {'input': [-4.822737153540387e-08, -4.631372565477899e-08, -4.438222495129211e-08, -4.2433614055232316e-08, -4.0468644193193375e-08, -3.848807289846209e-08, -3.64

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_42.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_42.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_1 delta x=1 160 delta x=1 40")